In [10]:
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json
!ls ~/.kaggle

kaggle.json


In [11]:
!pip install kaggle --upgrade


Requirement already up-to-date: kaggle in /usr/local/lib/python3.6/dist-packages (1.5.6)


In [12]:
!kaggle competitions download -c dl-cshse-fall2019-image-classification

100% 268M/269M [00:02<00:00, 150MB/s]
100% 269M/269M [00:02<00:00, 124MB/s]


In [15]:
!tar -xvzf simple_image_classification.tar.gz

simple_image_classification/
simple_image_classification/trainval/
simple_image_classification/trainval/trainval_43497.jpg
simple_image_classification/trainval/trainval_67828.jpg
simple_image_classification/trainval/trainval_02663.jpg
simple_image_classification/trainval/trainval_61459.jpg
simple_image_classification/trainval/trainval_50455.jpg
simple_image_classification/trainval/trainval_88210.jpg
simple_image_classification/trainval/trainval_00327.jpg
simple_image_classification/trainval/trainval_63014.jpg
simple_image_classification/trainval/trainval_10452.jpg
simple_image_classification/trainval/trainval_85311.jpg
simple_image_classification/trainval/trainval_02679.jpg
simple_image_classification/trainval/trainval_96164.jpg
simple_image_classification/trainval/trainval_54207.jpg
simple_image_classification/trainval/trainval_27767.jpg
simple_image_classification/trainval/trainval_63523.jpg
simple_image_classification/trainval/trainval_14810.jpg
simple_image_classification/trainval/

In [0]:
import pandas as pd
import numpy as np
import torch
y_train = pd.read_csv('simple_image_classification/labels_trainval.csv')

In [36]:
y_train

Id  Category
0      trainval_00000.jpg         7
1      trainval_00001.jpg       198
2      trainval_00002.jpg       161
3      trainval_00003.jpg       131
4      trainval_00004.jpg       107
5      trainval_00005.jpg       194
6      trainval_00006.jpg        77
7      trainval_00007.jpg        73
8      trainval_00008.jpg       150
9      trainval_00009.jpg         2
10     trainval_00010.jpg        59
11     trainval_00011.jpg        83
12     trainval_00012.jpg       158
13     trainval_00013.jpg        14
14     trainval_00014.jpg        35
15     trainval_00015.jpg       135
16     trainval_00016.jpg       130
17     trainval_00017.jpg        40
18     trainval_00018.jpg       131
19     trainval_00019.jpg       189
20     trainval_00020.jpg       172
21     trainval_00021.jpg       190
22     trainval_00022.jpg        17
23     trainval_00023.jpg       186
24     trainval_00024.jpg        17
25     trainval_00025.jpg       182
26     trainval_00026.jpg        56
27     trainval_00027.jpg       196
28     trainval_00028.jpg        69
29     trainval_00029.jpg       122
...                   ...       ...
99970  trainval_99970.jpg       142
99971  trainval_99971.jpg       183
99972  trainval_99972.jpg       170
99973  trainval_99973.jpg       187
99974  trainval_99974.jpg        52
99975  trainval_99975.jpg       147
99976  trainval_99976.jpg         6
99977  trainval_99977.jpg       157
99978  trainval_99978.jpg       132
99979  trainval_99979.jpg        60
99980  trainval_99980.jpg        57
99981  trainval_99981.jpg        24
99982  trainval_99982.jpg         7
99983  trainval_99983.jpg         8
99984  trainval_99984.jpg       110
99985  trainval_99985.jpg       154
99986  trainval_99986.jpg        22
99987  trainval_99987.jpg       142
99988  trainval_99988.jpg       194
99989  trainval_99989.jpg       177
99990  trainval_99990.jpg        26
99991  trainval_99991.jpg       193
99992  trainval_99992.jpg        36
99993  trainval_99993.jpg        58
99994  trainval_99994.jpg        64
99995  trainval_99995.jpg        72
99996  trainval_99996.jpg       194
99997  trainval_99997.jpg         6
99998  trainval_99998.jpg        29
99999  trainval_99999.jpg       167

[100000 rows x 2 columns]

In [0]:
import matplotlib.pyplot as plt
import os
x_train = []
for image in os.listdir('simple_image_classification/trainval'):
  x_train.append(plt.imread('simple_image_classification/trainval/{}'.format(image)))

In [0]:
x_train = torch.tensor(x_train)

In [31]:
x_train.data

tensor([[[[137, 127, 100],
          [129, 123,  89],
          [ 86,  87,  47],
          ...,
          [201, 227, 252],
          [200, 225, 255],
          [200, 225, 255]],

         [[121, 111,  86],
          [112, 105,  77],
          [ 97,  96,  65],
          ...,
          [202, 228, 255],
          [201, 226, 255],
          [201, 226, 255]],

         [[129, 119,  94],
          [124, 117,  91],
          [127, 126,  96],
          ...,
          [202, 227, 255],
          [202, 228, 255],
          [202, 228, 255]],

         ...,

         [[ 72,  74,  86],
          [ 88,  91, 100],
          [ 77,  80,  89],
          ...,
          [193, 171, 134],
          [200, 181, 148],
          [186, 169, 141]],

         [[ 82,  84,  96],
          [ 78,  81,  90],
          [ 87,  90,  99],
          ...,
          [206, 188, 150],
          [190, 175, 144],
          [200, 190, 165]],

         [[ 85,  87,  99],
          [ 85,  88,  97],
          [ 87,  90,  99],
         

In [0]:
import torchvision.models as models

resnet = models.resnet18()

In [0]:
resnet.fc = torch.nn.Linear(resnet.fc.in_features,199)

In [0]:
import time
def train_model(model, criterion, optimizer, scheduler, dataloaders, num_epochs=25):
    since = time.time()

    best_model_wts = model.state_dict()
    best_acc = 0.0

    for epoch in range(num_epochs):
        print('Epoch {}/{}'.format(epoch, num_epochs - 1))
        print('-' * 10)

        # Each epoch has a training and validation phase
        for phase in ['train', 'val']:
            if phase == 'train':
                scheduler.step()
                model.train(True)  # Set model to training mode
            else:
                model.train(False)  # Set model to evaluate mode

            running_loss = 0.0
            running_corrects = 0

            # Iterate over data.
            for data in dataloaders[phase]:
                # get the inputs
                inputs, labels = data

                if use_gpu:
                    inputs = inputs.cuda()
                    labels = labels.cuda()

                # zero the parameter gradients
                optimizer.zero_grad()

                # forward
                outputs = model(inputs)
                _, preds = torch.max(outputs, 1)
                loss = criterion(outputs, labels)

                # backward + optimize only if in training phase
                if phase == 'train':
                    loss.backward()
                    optimizer.step()

                # statistics
                running_loss += loss.item()
                running_corrects += torch.sum(preds == labels).type(torch.float)

            epoch_loss = running_loss / dataset_sizes[phase]
            epoch_acc = running_corrects / dataset_sizes[phase]

            print('{} Loss: {:.4f} Acc: {:.4f}'.format(
                phase, epoch_loss, epoch_acc))

            # deep copy the model
            if phase == 'val' and epoch_acc > best_acc:
                best_acc = epoch_acc
                best_model_wts = model.state_dict()
        
        time_elapsed = time.time() - since
        print('Elapsed {:.0f}m {:.0f}s\n'.format(time_elapsed // 60, time_elapsed % 60))

    time_elapsed = time.time() - since
    print('Training complete in {:.0f}m {:.0f}s'.format(
        time_elapsed // 60, time_elapsed % 60))
    print('Best val Acc: {:4f}'.format(best_acc))

    # load best model weights
    model.load_state_dict(best_model_wts)
    return model

In [0]:
params_to_train = resnet.parameters()
criterion = torch.nn.CrossEntropyLoss()
optimizer_ft = torch.optim.SGD(params_to_train, lr=0.001, momentum=0.9)
exp_lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer_ft, step_size=7, gamma=0.1)

In [0]:
image_datasets = {x: datasets.ImageFolder(os.path.join(data_dir, x),
                                          data_transforms[x])

In [50]:
model_ft = train_model(
    resnet, criterion, optimizer_ft, exp_lr_scheduler, num_epochs=50)

Epoch 0/49
----------


/usr/local/lib/python3.6/dist-packages/torch/optim/lr_scheduler.py:82: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule.See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  "https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate", UserWarning)


NameError: ignored